In [1]:
import sys
path2cpp_pkg = "/Users/mariusmahiout/Documents/repos/ising_core/build"
sys.path.append(path2cpp_pkg)
import ising

import os
os.chdir("/Users/mariusmahiout/Documents/repos/ising_core/python")

import src.misc_plotting as plotting
import src.utils as utils
import src.model_eval as eval
import src.isingfitter as fitter

import matplotlib.pyplot as plt
import time
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

In [2]:
def plot_generalized(layout_spec):
    
    num_rows = max([r for (r,_) in layout_spec.keys()])
    num_cols = max([c for (_,c) in layout_spec.keys()])
    
    fig = make_subplots(rows=num_rows, cols=num_cols, horizontal_spacing=0.1, vertical_spacing=0.1)

    curve_color = 'rgba(250, 150, 0, 1)'
    fill_color = 'rgba(250, 150, 0, 0.5)'


    for (r, c), specs in layout_spec.items():

        data = specs['data']
        data = [a.flatten() for a in data]
        label = specs['label']
        

        av_data = np.mean(data, axis=1)
        min_data = np.min(data, axis=1)
        max_data = np.max(data, axis=1)
        steps = list(range(len(av_data)))

        fig.add_trace(go.Scatter(x=steps, y=av_data, mode='lines', name=f'Av. {label}', line=dict(color=curve_color)), row=r, col=c)
        fig.add_trace(go.Scatter(x=steps, y=min_data, mode='lines', line=dict(width=0), hoverinfo='skip'), row=r, col=c)
        fig.add_trace(go.Scatter(x=steps, y=max_data, mode='lines', fill='tonexty', fillcolor=fill_color, line=dict(width=0), hoverinfo='skip'), row=r, col=c)

        fig.update_xaxes(title_text="Step", row=r, col=c)
        fig.update_yaxes(title_text=label.capitalize(), row=r, col=c)

    fig.update_layout(height=400 * num_rows, width=400 * num_cols, showlegend=False)

    fig.show()
    #display(fig)



In [11]:
num_units = 5
num_sims = 15000
num_burn = 1000
lr = 0.01
alpha = 0.01
tol = 1e-5
max_steps = 5000

In [6]:
##############
# SIMULATION #
##############

# setting up model
beta = 1.3
h = np.random.uniform(-.3 * beta, .3 * beta, num_units)
J = np.random.normal(0,  beta / np.sqrt(num_units), (num_units, num_units))
for i in range(num_units):
    J[i, i] = 0
    for j in range(i+1, num_units):
        J[j, i] = J[i, j]

true_model = ising.EqModel(J, h)

# simulating
true_sim = true_model.simulate(num_sims, num_burn)

# Gradient ascent

In [15]:
num_sims = 15000
num_burn = 1000
lr = 0.01
alpha = 0.01
tol = 1e-4
max_steps = 5000

In [16]:
#############
# INFERENCE #
#############

# setting up model
h_init = np.random.uniform(-1.5, 1.5, num_units)
J_init = np.random.normal(0,  1,  (num_units, num_units))
J_init = (J_init.T + J_init) * np.sqrt(2) / 2
np.fill_diagonal(J_init, 0)

ml_model = ising.EqModel(J_init, h_init)

ml_fitter = fitter.EqFitter(ml_model)
ml_fitter.TAP(true_sim)

# inference
ml_fitter.maximize_likelihood(
    sample=true_sim, 
    max_steps=max_steps, 
    learning_rate=lr,
    alpha=alpha,
    tolerance= tol, 
    num_sims=num_sims, 
    num_burn=num_burn,
    calc_llh=True
)


In [17]:
layout_spec = {
    (1, 1): {'data': ml_fitter.fields_grads, 'label': 'Fields gradient'},
    (2, 1): {'data': ml_fitter.couplings_grads, 'label': 'Couplings gradient'},
    (1, 2): {'data': ml_fitter.fields_diffs, 'label': 'Fields EMA diff.'},
    (2, 2): {'data': ml_fitter.couplings_diffs, 'label': 'Couplings EMA diff.'},
    (1, 3): {'data': ml_fitter.fields_history, 'label': 'Fields'},
    (2, 3): {'data': ml_fitter.couplings_history, 'label': 'Couplings'},
}

plot_generalized(layout_spec)

In [14]:
layout_spec = {
    (1, 1): {'data': ml_fitter.fields_grads, 'label': 'Fields gradient'},
    (2, 1): {'data': ml_fitter.couplings_grads, 'label': 'Couplings gradient'},
    (1, 2): {'data': ml_fitter.fields_diffs, 'label': 'Fields EMA diff.'},
    (2, 2): {'data': ml_fitter.couplings_diffs, 'label': 'Couplings EMA diff.'},
    (1, 3): {'data': ml_fitter.fields_history, 'label': 'Fields'},
    (2, 3): {'data': ml_fitter.couplings_history, 'label': 'Couplings'},
}

plot_generalized(layout_spec)